# XOR-5

Should do [Working efficiently with jupyter lab](https://florianwilhelm.info/2018/11/working_efficiently_with_jupyter_lab/)

In [1]:
%load_ext autoreload
%autoreload 2
%matplotlib widget
#%matplotlib inline

In [2]:
import numpy as np
import matplotlib.pyplot as plt
#import dill

In [3]:
from nn import Network, Layer, IdentityLayer, AffineLayer, MapLayer
from nnbench import NNBench
from nnvis import NNVis

___

In [4]:
net = Network()
net.extend(AffineLayer(2,2))
#leak = 0
#net.extend(MapLayer(lambda x: (x*(1+leak/2)+abs(x)*(1-leak/2))/2, lambda d: [leak,1][1 if d>0 else 0]))
#net.extend(MapLayer(lambda x: max(0, np.sign(x)) * x, lambda d: max(0, np.sign(d))))
net.extend(MapLayer(np.tanh, lambda d: 1.0 - np.tanh(d)**2))
net.extend(AffineLayer(2,1))
net.extend(MapLayer(np.tanh, lambda d: 1.0 - np.tanh(d)**2))
#sigmoid = lambda x: 1/(np.exp(x)+1)
#net.extend(MapLayer(sigmoid, lambda d: sigmoid(d)*(1-sigmoid(d))))
#net.extend(MapLayer(lambda x: max(0, np.sign(x)) * x, lambda d: max(0, np.sign(d))))

In [5]:
net.layers

In [6]:
bench = NNBench(net)
vis = NNVis(bench)

In [7]:
dat = \
[(np.array([-1,-1]), np.array([-1])),
 (np.array([-1,1]), np.array([1])),
 (np.array([1,1]), np.array([-1])),
 (np.array([1,-1]), np.array([1]))]
dc = 0
amp= 1
temp = [(d[0]*amp/2+dc,d[1]*amp/2+dc) for d in dat]

bench.training_data = ((np.array([v[0] for v in temp]),
                        np.array([v[1] for v in temp])),)
bench.training_data

((array([[-0.5, -0.5],
         [-0.5,  0.5],
         [ 0.5,  0.5],
         [ 0.5, -0.5]]),
  array([[-0.5],
         [ 0.5],
         [-0.5],
         [ 0.5]])),)

In [8]:
bench.training_data_gen = bench.training_data_gen_fixed

In [9]:
#list(bench.training_data_gen(2))

In [10]:
if False: # it would read in an old nn_v2 net
    with open('slow_xor_1.net', 'rb') as f:
        bench.net_checkpoint = f.read()
    bench.rollback_net()
else:
    bench.randomize_net()
    bench.checkpoint_net()

In [11]:
vis.plot_learning(100)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [12]:
bench.rollback_net()

In [13]:
bench.net.state_vector()

array([-0.28885892,  0.39697713,  0.18435844,  1.79452739,  1.17999128,
        0.47039108,  1.06932594, -0.25044494,  0.71638827])

In [14]:
vis.knobs_plot_learning(100)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

In [42]:
bench.rollback_net()

In [16]:
isv = interesting_stubborn_sv = np.array([-4.16013824, -4.37023452, -0.83547458,  0.92877501,  1.48893334,
        1.5066594 ,  1.10828375, -0.71174959,  0.16778073])

In [17]:
bench.net.set_state_from_vector(interesting_stubborn_sv)

In [18]:
net(bench.training_data[0][0])

array([[-0.10882398],
       [ 0.09770892],
       [ 0.07721691],
       [-0.0422585 ]])

In [19]:
learnings = bench.learn(100)
net(bench.training_data[0][0])

array([[-0.10882398],
       [ 0.09770892],
       [ 0.07721691],
       [-0.0422585 ]])

In [20]:
learnings = bench.learn(100)
net(bench.training_data[0][0])

array([[-0.10882398],
       [ 0.09770892],
       [ 0.07721691],
       [-0.0422585 ]])

In [21]:
bench.net.set_state_from_vector(interesting_stubborn_sv)

## Plot the loss surface with `plotly`

In [44]:
if True:
    #bench.randomize_net()
    bench.rollback_net()
    rates = np.logspace(-4, 0, num=100)
    cube = bench.learn_loss_cube(1000, rates)
    vis.plot_loss_cube()

## Plot the loss surface with `matplotlib`

In [23]:
#bench.mpl_plot_loss_cube()

## Tracks
Examine the trajectory in state space during learning, along state space, and the loss function.
Each learning iteration changes the net state. We can examine those deltas.
Questions:
1. Are there regimes of direction-of-change (DoC) in state space, or does the DoC wander chaotically?
1. What are the spectral characteristics of the DoC? Length characteristics?
1. How do the DoC characteristics relate to the loss function, and it's first difference?
1. How do these trajectories vary with learning rate? Are there clues in these to adapt the learning rate?
1. How do the trajectory characteristics vary across different starting nets?
1. How do these measures vary with the objective function of the learning process, that is, what you're trying to teach the net?
1. How do the different layers with learning state evolve? Do they settle at different times? How does an upstream layer change, as a consequence of learning, affect downstream layers? Down affect up?

### Analysis setup

`bench.learn_track(n)` does n batches of learning, recording the state vector of the network after each step.

In [24]:
bench.randomize_net()
bench.checkpoint_net()

In [25]:
bench.rollback_net()
bench.net.eta = 0.05
lt = bench.learn_track(2000)
lt[0], lt[-1]

((array([ 0.01488962,  0.33616689, -0.20216084,  0.68859005, -1.0362747 ,
         -0.82958655,  1.24649692, -0.26848513, -0.82837969]),
  4.409283301733615),
 (array([ 0.90542002,  1.86649538,  0.8864594 ,  1.8082128 ,  0.21844531,
         -1.09701953,  1.72424283, -1.4818975 , -1.00574007]),
  6.902576101604765e-22))

Wrangle the state-space trajectory and the losses into form.

In [26]:
trajectory = np.vstack([v[0] for v in lt])
losses = np.vstack([v[1] for v in lt])

Take first differences, which represent the changes at each step

In [27]:
traj_steps = np.diff(trajectory, axis=0)
loss_steps = np.diff(losses, axis=0)

In [28]:
traj_steps[:5]

array([[ 1.10874386e-03, -3.76491324e-05, -2.10266290e-03,
        -3.35023007e-04,  1.39124943e-02, -3.81829494e-03,
        -2.08641348e-02, -1.83097002e-02,  2.72077547e-02],
       [ 1.27246052e-03, -4.42620054e-05, -2.36145831e-03,
        -3.92024197e-04,  1.55267278e-02, -4.50768472e-03,
        -2.29898626e-02, -2.04015274e-02,  3.02160380e-02],
       [ 1.47915655e-03, -5.19418159e-05, -2.66713504e-03,
        -4.65377598e-04,  1.74712406e-02, -5.37732541e-03,
        -2.55092060e-02, -2.29238234e-02,  3.38299943e-02],
       [ 1.74452347e-03, -6.03582943e-05, -3.02532310e-03,
        -5.62469681e-04,  1.98275307e-02, -6.48808098e-03,
        -2.85065624e-02, -2.59855301e-02,  3.82001233e-02],
       [ 2.09084490e-03, -6.82412407e-05, -3.43509467e-03,
        -6.95308843e-04,  2.26850614e-02, -7.92148122e-03,
        -3.20661602e-02, -2.97092731e-02,  4.34950634e-02]])

Find the L2 norm of the trajectory steps $\lVert traj \rVert$:

In [29]:
traj_L2 = np.sqrt(np.einsum('...i,...i', traj_steps, traj_steps))

In [30]:
len(traj_L2), traj_L2[:5], traj_L2[-5:]

(1999,
 array([0.04152975, 0.04611415, 0.05161754, 0.05826546, 0.06630778]),
 array([7.38604691e-13, 7.28388020e-13, 7.18407176e-13, 7.08557530e-13,
        6.98818171e-13]))

Find the angles between trajectory steps, from
$$\mathbf {a} \cdot \mathbf {b} = \left\|\mathbf {a} \right\|\left\|\mathbf {b} \right\|\cos \theta \\
\cos \theta = \frac{\mathbf {a} \cdot \mathbf {b}}{\left\|\mathbf {a} \right\|\left\|\mathbf {b} \right\|} \\
$$
where $\mathbf {a}$ and $\mathbf {b}$ are a state-space trajectory step and the succeeding step respectively

Find $\mathbf {a} \cdot \mathbf {b}$:

In [31]:
trajn_dot_nplus1 = np.einsum('...i,...i', traj_steps[:-1], traj_steps[1:])
trajn_dot_nplus1[:5], np.any(trajn_dot_nplus1 < 0)

(array([0.00191506, 0.00238022, 0.00300739, 0.00386324, 0.00503576]), False)

Find $\left\|\mathbf {a} \right\|\left\|\mathbf {b} \right\|$:

In [32]:
traj_cos_denom = np.multiply(traj_L2[:-1], traj_L2[1:])

This will be the divisor. Some entries may be zero, so we adapt

In [33]:
len(traj_L2) - np.count_nonzero(traj_L2)

0

In [34]:
np.equal(traj_L2, 0)

array([False, False, False, ..., False, False, False])

Find $\cos \theta$ by dividing, excluding division by zero:

In [35]:
traj_cos = np.divide(trajn_dot_nplus1, traj_cos_denom, where=traj_cos_denom!=0.0)
traj_cos[:5], traj_cos[-5:], min(traj_cos), max(traj_cos)

(array([0.99997243, 0.99996609, 0.99995752, 0.99994563, 0.99992851]),
 array([0.99999995, 0.99999992, 0.99999993, 0.99999994, 0.99999991]),
 0.9701026325666583,
 1.0000000000000002)

In [36]:
#traj_theta = np.arccos(traj_cos)
#traj_theta[:5], traj_theta[-5:]

In [37]:
# Development space for plotting:
if True:
    fig, ax = plt.subplots()  # Create a figure and an axes.
    traj_color = 'xkcd:red'
    loss_color = 'xkcd:blue'
    cos_color = 'xkcd:green'
    ax.set_xlabel('$n$')  # Add an x-label to the axes.
    ax.set_ylabel('$|\Delta state|$', color=traj_color)
    ax.tick_params(axis='y', labelcolor=traj_color)
    ax.set_title(f"$\eta={bench.net.eta}$")  # Add a title to the axes.
    ax.set_yscale('log')
    tnl, = ax.plot(traj_L2, label=f"traj norm", color=traj_color)  # Plot some data on the axes.
    ax2 = ax.twinx()  # instantiate a second axes that shares the same x-axis
    ax2.tick_params(axis='y', labelcolor=loss_color)
    dll, = ax2.plot(loss_steps, label=f"$\Delta loss$", color=loss_color)  # Plot some data on the axes.
    cosl, = ax2.plot(traj_cos, label=f"$\Delta state cosine$", color=cos_color)
    ax.legend([tnl, dll, cosl], ["$\\|\\Delta state \\|$", "$\\Delta loss$", "$cos(\\theta)\Delta$"])  # Add a legend.
    #ax2.legend()  # Add a legend.
    fig.tight_layout()  # otherwise the right y-label is slightly clipped
    plt.show()
 

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

---

# Scratch